In [1]:
import random
from IPython.core.display import SVG
import pyomo.environ as pyo
from pysat.solvers import Solver
from pysat.formula import CNF 
import py_svg_combinatorics as psc
from ipywidgets import widgets, HBox
from collections import Counter
from pprint import pprint
from random import randint
import numpy as np
from IPython.display import IFrame
import IPython
from copy import copy
import os
from pathlib import Path
np.set_printoptions(precision=2)
np.set_printoptions(suppress=True)
nbname = ''
try:
    nbname = __vsc_ipynb_file__
except:
    if 'COCALC_JUPYTER_FILENAME' in os.environ:
        nbname = os.environ['COCALC_JUPYTER_FILENAME']    
title_ = Path(nbname).stem.replace('-', '_').title()    
IFrame(f'https://discopal.ispras.ru/index.php?title=Hardprob/{title_}&useskin=cleanmonobook', width=1280, height=300)

In [2]:
# Случайные данные
m = np.random.randint(3, 20)
n = np.random.randint(3, 20)
A = np.random.rand(m, n)
c = np.random.rand(n)
b = 1/np.random.rand(m)

A, b, c


(array([[0.28, 0.04, 0.76],
        [0.06, 0.17, 0.85],
        [0.31, 0.82, 0.01],
        [0.46, 0.76, 0.13],
        [0.82, 0.48, 0.67],
        [0.77, 0.28, 0.28],
        [0.09, 0.86, 0.62],
        [0.56, 0.76, 0.83],
        [0.01, 0.94, 0.3 ],
        [0.01, 0.86, 0.33],
        [0.59, 0.91, 0.91],
        [0.94, 0.28, 0.13]]),
 array([10.21,  2.84,  3.5 ,  1.52,  4.71,  1.77,  1.16,  2.74, 33.54,
         1.65,  4.09,  7.72]),
 array([0.19, 0.02, 0.93]))

In [3]:
def get_model(A, b, c):
    m = pyo.ConcreteModel()

    m.m, m.n = A.shape

    # на всякий случай, возьмем с собой
    m.A = A
    m.b = b
    m.c = c
    
    m.I = range(m.m)
    m.J = range(m.n)
    
    m.x = pyo.Var(m.J, domain=pyo.Binary)
    m.obj = pyo.Objective(expr = sum( c[j] * m.x[j] for j in m.J), sense=pyo.maximize)

    @m.Constraint(m.I)
    def не_больше(m, i):
        return sum(A[i, j] * m.x[j] for j in m.J) <= b[i]

    return m

m = get_model(A, b, c)
m.pprint()

2 Set Declarations
    x_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :    3 : {0, 1, 2}
    не_больше_index : Size=1, Index=None, Ordered=Insertion
        Key  : Dimen : Domain : Size : Members
        None :     1 :    Any :   12 : {0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11}

1 Var Declarations
    x : Size=3, Index=x_index
        Key : Lower : Value : Upper : Fixed : Stale : Domain
          0 :     0 :  None :     1 : False :  True : Binary
          1 :     0 :  None :     1 : False :  True : Binary
          2 :     0 :  None :     1 : False :  True : Binary

1 Objective Declarations
    obj : Size=1, Index=None, Active=True
        Key  : Active : Sense    : Expression
        None :   True : maximize : 0.18665218449400867*x[0] + 0.022131302476188552*x[1] + 0.9332152905432948*x[2]

1 Constraint Declarations
    не_больше : Size=12, Index=не_больше_index, Active=True
        Key : Lower : Body             

In [4]:
def print_solution(m):
    for v in m.component_data_objects(pyo.Var):
        if v.value and v.value > 0:
            print(str(v), v.value)

In [5]:
solver = pyo.SolverFactory('cbc')
solver.solve(m).write()
print_solution(m)

# ==========================================================
# = Solver Results                                         =
# ==========================================================
# ----------------------------------------------------------
#   Problem Information
# ----------------------------------------------------------
Problem: 
- Name: unknown
  Lower bound: 1.11986748
  Upper bound: 1.11986748
  Number of objectives: 1
  Number of constraints: 1
  Number of variables: 3
  Number of binary variables: 3
  Number of integer variables: 3
  Number of nonzeros: 3
  Sense: maximize
# ----------------------------------------------------------
#   Solver Information
# ----------------------------------------------------------
Solver: 
- Status: ok
  User time: -1.0
  System time: 0.0
  Wallclock time: 0.0
  Termination condition: optimal
  Termination message: Model was solved to optimality (subject to tolerances), and an optimal solution is available.
  Statistics: 
    Branch and bo